# Modelling, Simulation and Optimization
### Ridwan Atanda
### School of Computing
### National College of Ireland 
### Student ID: X19142366


 

<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Import-Libraries" data-toc-modified-id="Import-Libraries-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Import Libraries</a></span></li><li><span><a href="#Prepare-Data" data-toc-modified-id="Prepare-Data-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Prepare Data</a></span></li><li><span><a href="#Prepare-Passengers-Data" data-toc-modified-id="Prepare-Passengers-Data-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Prepare Passengers Data</a></span></li><li><span><a href="#Train-Process" data-toc-modified-id="Train-Process-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Train Process</a></span></li><li><span><a href="#Boarding-Process" data-toc-modified-id="Boarding-Process-5"><span class="toc-item-num">5&nbsp;&nbsp;</span>Boarding Process</a></span></li><li><span><a href="#Signaling-Blocks" data-toc-modified-id="Signaling-Blocks-6"><span class="toc-item-num">6&nbsp;&nbsp;</span>Signaling Blocks</a></span></li><li><span><a href="#The-Network" data-toc-modified-id="The-Network-7"><span class="toc-item-num">7&nbsp;&nbsp;</span>The Network</a></span></li><li><span><a href="#Simulation" data-toc-modified-id="Simulation-7"><span class="toc-item-num">7&nbsp;&nbsp;</span>Simulation</a></span></li><li><span><a href="#Optimization" data-toc-modified-id="Optimization-8"><span class="toc-item-num">8&nbsp;&nbsp;</span>Optimization</a></span><ul class="toc-item"><li><span><a href="#Part-1" data-toc-modified-id="Part-1-8.1"><span class="toc-item-num">8.1&nbsp;&nbsp;</span>Part-1</a></span></li><li><span><a href="#Part-2" data-toc-modified-id="Part-2-8.2"><span class="toc-item-num">8.2&nbsp;&nbsp;</span>Part-2</a></span></li></ul><li><span><a href="#Discussion-and-Results" data-toc-modified-id="Discussion-and-Results-9"><span class="toc-item-num">9&nbsp;&nbsp;</span>Discussion and Results</a></span></li><li><span><a href="#References" data-toc-modified-id="References-9"><span class="toc-item-num">10&nbsp;&nbsp;</span>References</a></span></li>

# Import Libraries 

In [1]:
import pandas as pd
import matplotlib as mpl
import matplotlib.pyplot as plt
import scipy.stats as stats
import math
import numpy as np
import simpy
import simpy.events as evt
import random

# Prepare Data 

Given Parameters:

Let D1 be Distance London Euston to London Old Oak Common = ?

Let D2 be Distance London Old Oak Common to Birmingham Interchange = 145km

Let D3 be Distance Birmingham Interchange to Birmingham Curzon Street = ?

let T1 be Time London Euston to London Old Oak Common = 5min

Let T2 be Time London Old Oak Common to Birmingham Interchange = 31min

Let T3 be Time Birmingham Interchange to Birmingham Curzon Street = 9min

Given the above parameters, we implement a simple arithmetic operation to calculate D1 and D3, and convert the km to m

D1 = 23.4, D3 = 42.1

1km = 1000m,
23.4km = 23400m,
145km = 145000m,
42.1km = 42100m

Convert running times into seconds 

1min = 60 secs,
5min = 300secs,
31min = 1860secs,
9min = 540secs,



In [2]:
#Initialize data of list 

data =  {'Line':['HS2', 'HS2', 'HS2'], 'From':['London Euston', 'London Old Oak Common', 'Birmingham Interchange'], 
        'To': ['London Old Oak Common', 'Birmingham Interchange', 'Birmingham Curzon Street'], 'Distance (m)': [23400, 145000, 42100],
        'Time': [300,1860,540], 'Delay': [300,300,300], 'Signaling Blocks': [1,14,2]}

#Create Data frame 

df = pd.DataFrame(data) 
df

Line                    From                        To  Distance (m)  Time  \
0  HS2           London Euston     London Old Oak Common         23400   300   
1  HS2   London Old Oak Common    Birmingham Interchange        145000  1860   
2  HS2  Birmingham Interchange  Birmingham Curzon Street         42100   540   

   Delay  Signaling Blocks  
0    300                 1  
1    300                14  
2    300                 2

In [3]:
#Record all Simulation result 

results = pd.DataFrame({'departure':[],'arrival':[],'passengers':[],'travel_time':[]})
results

Empty DataFrame
Columns: [departure, arrival, passengers, travel_time]
Index: []

# Prepare Passengers Data 

In [4]:
#Prepare customers data using Poisson Distribution

def poissonEvents(λ=None, N=None, T=None, 
                  plot=True, events=None, figsize=None):

    if events!=None:
        N = len(events)
        
    if N!=None and T==None and λ!=None:
        T = int(N/λ)
    elif N==None and T!=None and λ!=None:
        N = int(λ*T)
    elif N!=None and T!=None and λ==None:
        λ = N/T
    
   
    if events==None:
        u = [ random.uniform(0, 1) for i in range(N) ]
        P = list(np.cumsum(list(map(
                lambda x: -math.log(1-x)/λ, u))))
    else:
        P = events
        
    if plot:
  
        if figsize!=None:
            width, height = figsize
        else:
            width, height = 10, 6
            
        fig, ax=plt.subplots(1,1)
        fig.set_figwidth(width)
        fig.set_figheight(height)
        
        def X(l):
            
            xmax = max(int(N/λ),math.ceil(max(l)))
            
            def double(l):
                return [] if l==[] \
                        else [l[0], l[0]]+double(l[1:])
    
            return [0]+double(l)+[xmax]
        
        def Y(l):
    
            def steps(l, n):
                return [] if l==[] \
                        else [n, n]+steps(l[1:], n+1)
    
            return [0, 0]+steps(l, 1)
    
        x = X(P)
        y = Y(P)

        ax.set_title(f"Poisson Process λ={λ:5.3f} n={N:d}")
        ax.set_xlim(min(x), max(x))
        ax.set_ylim(min(y), max(y))
        ax.yaxis.set_major_locator(
            mpl.ticker.MaxNLocator(integer=True))
        ax.plot(x, y, lw=3)
        ax.plot(x, list(map(lambda x:λ*x, x)))
        ax.grid(True)
        
    return P

In [5]:
#Define function that calls the poisson event to generate Customer data
# we set λ=100/3600 to get a maximum of 100 customers per hour 
# In total we generate 300 passengers as N is set to 100 for each stations 
def Pass():
    
    passengers_euston = poissonEvents(λ=100/3600, N=100, plot=False) 
    euston = pd.DataFrame({'station':['London Euston']*len(passengers_euston), 'arr':passengers_euston})

    passengers_oak = poissonEvents(λ=100/3600, N=100, plot=False)
    oak = pd.DataFrame({'station':['London Old Oak Common']*len(passengers_oak), 'arr':passengers_oak})

    passengers_interchange = poissonEvents(λ=100/3600, N=100, plot=False)
    interchange = pd.DataFrame({'station':['Birmingham Interchange']*len(passengers_interchange), 'arr':passengers_interchange})

    passengers = euston.append(oak)
    passengers = passengers.append(interchange)
    
    return passengers

# Train Process 

In [6]:
class Train:  
    def __init__(self, i, route, d): # maxPassengers=400
        self.name ='[Train '+f"{i:2d}"+']'
        self.route = route
        self.r = i
        self.p     = 0
       # self.maxP  = maxPassengers
        self.blocks = d
    
    def process(self):
        
        print(f"{now():s} {self.name:s} drives to starting location")
        yield env.timeout(60)
        startingstation = self.route[0]   # starting location
        i=0
        results.at[self.r,'departure'] = env.now
        num = board(startingstation,env.now)
        self.p += num
        print(f"{now():s} {self.name:s} {num} passengers boarded")
        yield env.timeout(num*3) # num is the total number of passengers boarded and 
        #each passengers take 3 seconds to get on board 
        
        print(f"{now():s} {self.name:s} dep {startingstation:s}")
        for dest in self.route[1:]:
            data=df[df['From']==startingstation]
            travelTime=data.iloc[0].at['Time']
            sig=data.iloc[0].at['Signaling Blocks']
            delay=data.iloc[0].at['Delay']
            blocks = self.blocks[i]
            block_travel = travelTime/sig
            
            l = 1
            #yield env.timeout(delay)
            
            for block in blocks:
                with block.request() as req:
                    yield req
                    
                    print(f"{now():s} {self.name:s} enters block {l:d} for {dest:s}") 
                    
                    yield env.timeout(block_travel)

                    if l == len(blocks):
                        print(f"{now():s} {self.name:s} arr {dest:s}")
                        num = board(dest,env.now)
                        self.p += num
                        print(f"{now():s} {self.name:s} {num} passengers boarded")
                        yield env.timeout(num*3)
                        startingstation=dest
                        
                    if startingstation == "Birmingham Curzon Street":
                        print(f"{now():s} {self.name:s} arr final station") #no passengers will get on board at the final station
                        results.at[self.r,'arrival'] = env.now
                        results.at[self.r,'passengers'] = self.p
                        results.at[self.r,'travel_time'] = results.at[self.r,'arrival']-results.at[self.r,'departure']
                    
                l+=1         
                    
            i+=1
          
   
    

# Boarding Process

In [7]:
#Number of passengers at the station when the train arrives 

def board(station,s):
    
    df = passengers[passengers['station'] == station]
    t = df['arr']
    g = s-21600
    passengercount = 0
    for arr in t:
        if arr>0 and arr<=g:
            passengercount+=1
            passengers.arr = passengers.arr.replace(arr,0)
    
    return passengercount
            

# Signaling Blocks 

In [8]:
def block():
    blocks = []
    stations = df['From'].to_list()
    stations += [df['To'].to_list()[-1]]
    startingBlock = stations[0] # STARTING LOCATION
    for dest in stations[1:]:
        data = df[df['From'] == startingBlock]
        sb = data.iloc[0].at['Signaling Blocks']
        destb = []
        for i in range(sb):
            block = simpy.Resource(env, capacity = 1)
            destb.append(block)
        blocks.append(destb)
        startingBlock = dest 
    return blocks

# The Network

In [9]:
#Instantiate the train class, here we define class that calls and release the trains for every stations 

def line(d, start=6*3600, stop=7*3600, timing=180):
    stations=df['From'].to_list()
    stations+=[df['To'].to_list()[-1]]
    yield env.timeout(start-env.now) # the line starts operating at 6am
    for i in range(int((stop-start)/timing)):
        t=Train(i, stations, d)
        env.process(t.process())
        yield env.timeout(timing)

In [10]:
#format Date and Time 
def daytime(t):
    t=int(t)
    return f"{t//3600:02d}:{(t%3600)//60:02d}:{t%60:02d}"
def now():
    return daytime(env.now)

In [11]:
def runsimulation(a,b):
    global passengers
    global env
    global results
    
    df.iloc[1,6]=b
    passengers= Pass()
    env = simpy.Environment()
    
    d = block() 
    env.process(line(d))
    env.run()
    
    return results
    
    

Factors to optimize are the mean average travelling time and the maximum numbers of passengers in peak hours 

In [12]:
def stats(results):
    
    return np.mean(results['travel_time']), np.sum(results['passengers'])
    

# Simulation 

The train network is scheduled for 20 trains per hour and 14 signaling blocks. This result will be fed Monte Carlo for optimization problem.

In [13]:
runsimulation(20,14) 

06:00:00 [Train  0] drives to starting location
06:01:00 [Train  0] 6 passengers boarded
06:01:18 [Train  0] dep London Euston
06:01:18 [Train  0] enters block 1 for London Old Oak Common
06:03:00 [Train  1] drives to starting location
06:04:00 [Train  1] 8 passengers boarded
06:04:24 [Train  1] dep London Euston
06:06:00 [Train  2] drives to starting location
06:06:18 [Train  0] arr London Old Oak Common
06:06:18 [Train  0] 15 passengers boarded
06:07:00 [Train  2] 10 passengers boarded
06:07:03 [Train  0] enters block 1 for Birmingham Interchange
06:07:03 [Train  1] enters block 1 for London Old Oak Common
06:07:30 [Train  2] dep London Euston
06:09:00 [Train  3] drives to starting location
06:09:15 [Train  0] enters block 2 for Birmingham Interchange
06:10:00 [Train  3] 5 passengers boarded
06:10:15 [Train  3] dep London Euston
06:11:28 [Train  0] enters block 3 for Birmingham Interchange
06:12:00 [Train  4] drives to starting location
06:12:03 [Train  1] arr London Old Oak Common
0

07:10:41 [Train  6] enters block 1 for Birmingham Curzon Street
07:10:43 [Train 11] enters block 3 for Birmingham Interchange
07:11:18 [Train 12] arr London Old Oak Common
07:11:18 [Train 12] 0 passengers boarded
07:11:18 [Train 12] enters block 1 for Birmingham Interchange
07:11:18 [Train 13] enters block 1 for London Old Oak Common
07:11:23 [Train  9] enters block 8 for Birmingham Interchange
07:11:40 [Train  7] enters block 13 for Birmingham Interchange
07:12:16 [Train 10] enters block 6 for Birmingham Interchange
07:12:38 [Train  8] enters block 11 for Birmingham Interchange
07:12:56 [Train 11] enters block 4 for Birmingham Interchange
07:13:30 [Train 12] enters block 2 for Birmingham Interchange
07:13:36 [Train  9] enters block 9 for Birmingham Interchange
07:13:53 [Train  7] enters block 14 for Birmingham Interchange
07:14:17 [Train  5] arr Birmingham Curzon Street
07:14:17 [Train  5] 0 passengers boarded
07:14:17 [Train  5] arr final station
07:14:29 [Train 10] enters block 7 fo

departure  arrival  passengers  travel_time
0     21660.0  24603.0        81.0       2943.0
1     21840.0  24873.0        29.0       3033.0
2     22020.0  25143.0        34.0       3123.0
3     22200.0  25452.0        29.0       3252.0
4     22380.0  25740.0        13.0       3360.0
5     22560.0  26058.0        14.0       3498.0
6     22740.0  26382.0        16.0       3642.0
7     22920.0  26706.0        14.0       3786.0
8     23100.0  27030.0        12.0       3930.0
9     23280.0  27354.0        13.0       4074.0
10    23460.0  27672.0        11.0       4212.0
11    23640.0  27978.0        10.0       4338.0
12    23820.0  28278.0         8.0       4458.0
13    24000.0  28578.0         9.0       4578.0
14    24180.0  28878.0         1.0       4698.0
15    24360.0  29178.0         6.0       4818.0
16    24540.0  29478.0         0.0       4938.0
17    24720.0  29778.0         0.0       5058.0
18    24900.0  30078.0         0.0       5178.0
19    25080.0  30378.0         0.0       5298.0

In [14]:
stats(results)

(4110.749999999976, 300.0)

# Optimization 

In [15]:
#Monte Carlo Optimization method

def monte_carlo(n, xmin, xmax, ymin, ymax):
    x = [ random.randint(xmin, xmax) for i in range(n)]
    y = [ random.randint(ymin, ymax) for i in range(n)]
    xp = [ x[0] ]
    yp = [ y[0] ]
    
    #simulate
    res = runsimulation(x[0],y[0])
    avg, _ = stats(res)
    
    for i in range(1, len(x)):
        #simulate
        res = runsimulation(x[i],y[i])
        n_avg, _ = stats(res) 
        if n_avg < avg:
            xp += [x[i]]
            yp += [y[i]]
            avg = n_avg
    
    #simulate
    res = runsimulation(xp[-1],yp[-1])
    ag, _ = stats(res)
    
            
    return len(xp), xp[-1], yp[-1],ag

## Part-1

Minimize overall average travel time using Monte Carlo

In [16]:
monte_carlo(100,1,20,1,15) #run simulation 100 times for min of 1 train and max of 20 trains, min of 1 signaling blocks and max of 15

06:00:00 [Train  0] drives to starting location
06:01:00 [Train  0] 2 passengers boarded
06:01:06 [Train  0] dep London Euston
06:01:06 [Train  0] enters block 1 for London Old Oak Common
06:03:00 [Train  1] drives to starting location
06:04:00 [Train  1] 5 passengers boarded
06:04:15 [Train  1] dep London Euston
06:06:00 [Train  2] drives to starting location
06:06:06 [Train  0] arr London Old Oak Common
06:06:06 [Train  0] 12 passengers boarded
06:06:42 [Train  0] enters block 1 for Birmingham Interchange
06:06:42 [Train  1] enters block 1 for London Old Oak Common
06:07:00 [Train  2] 9 passengers boarded
06:07:27 [Train  2] dep London Euston
06:09:00 [Train  3] drives to starting location
06:10:00 [Train  3] 7 passengers boarded
06:10:21 [Train  3] dep London Euston
06:11:42 [Train  1] arr London Old Oak Common
06:11:42 [Train  1] 11 passengers boarded
06:12:00 [Train  4] drives to starting location
06:12:15 [Train  2] enters block 1 for London Old Oak Common
06:13:00 [Train  4] 5 p

09:48:42 [Train 13] enters block 2 for Birmingham Interchange
09:53:12 [Train 12] enters block 2 for Birmingham Curzon Street
09:57:42 [Train 12] arr Birmingham Curzon Street
09:57:42 [Train 12] 0 passengers boarded
09:57:42 [Train 12] arr final station
09:59:12 [Train 15] enters block 1 for Birmingham Interchange
10:04:12 [Train 13] arr Birmingham Interchange
10:04:12 [Train 13] 0 passengers boarded
10:04:12 [Train 13] enters block 1 for Birmingham Curzon Street
10:04:12 [Train 14] enters block 2 for Birmingham Interchange
10:08:42 [Train 13] enters block 2 for Birmingham Curzon Street
10:13:12 [Train 13] arr Birmingham Curzon Street
10:13:12 [Train 13] 0 passengers boarded
10:13:12 [Train 13] arr final station
10:14:42 [Train 16] enters block 1 for Birmingham Interchange
10:19:42 [Train 14] arr Birmingham Interchange
10:19:42 [Train 14] 0 passengers boarded
10:19:42 [Train 14] enters block 1 for Birmingham Curzon Street
10:19:42 [Train 15] enters block 2 for Birmingham Interchange
10

08:41:30 [Train 10] enters block 1 for Birmingham Interchange
08:46:30 [Train  8] arr Birmingham Interchange
08:46:30 [Train  8] 0 passengers boarded
08:46:30 [Train  8] enters block 1 for Birmingham Curzon Street
08:46:30 [Train  9] enters block 2 for Birmingham Interchange
08:51:00 [Train  8] enters block 2 for Birmingham Curzon Street
08:55:30 [Train  8] arr Birmingham Curzon Street
08:55:30 [Train  8] 0 passengers boarded
08:55:30 [Train  8] arr final station
08:57:00 [Train 11] enters block 1 for Birmingham Interchange
09:02:00 [Train  9] arr Birmingham Interchange
09:02:00 [Train  9] 0 passengers boarded
09:02:00 [Train  9] enters block 1 for Birmingham Curzon Street
09:02:00 [Train 10] enters block 2 for Birmingham Interchange
09:06:30 [Train  9] enters block 2 for Birmingham Curzon Street
09:11:00 [Train  9] arr Birmingham Curzon Street
09:11:00 [Train  9] 0 passengers boarded
09:11:00 [Train  9] arr final station
09:12:30 [Train 12] enters block 1 for Birmingham Interchange
09

06:54:03 [Train  2] enters block 2 for Birmingham Curzon Street
06:54:07 [Train  5] enters block 9 for Birmingham Interchange
06:54:33 [Train  6] enters block 7 for Birmingham Interchange
06:54:50 [Train  7] enters block 5 for Birmingham Interchange
06:54:54 [Train  9] arr London Old Oak Common
06:54:54 [Train  9] 5 passengers boarded
06:55:00 [Train 18] 1 passengers boarded
06:55:03 [Train 18] dep London Euston
06:55:04 [Train  8] enters block 3 for Birmingham Interchange
06:55:09 [Train  9] enters block 1 for Birmingham Interchange
06:55:09 [Train 10] enters block 1 for London Old Oak Common
06:56:16 [Train  4] enters block 12 for Birmingham Interchange
06:56:42 [Train  5] enters block 10 for Birmingham Interchange
06:57:00 [Train 19] drives to starting location
06:57:08 [Train  6] enters block 8 for Birmingham Interchange
06:57:25 [Train  7] enters block 6 for Birmingham Interchange
06:57:39 [Train  8] enters block 4 for Birmingham Interchange
06:57:44 [Train  9] enters block 2 for 

06:37:32 [Train  0] 70 passengers boarded
06:37:33 [Train  1] enters block 10 for Birmingham Interchange
06:37:37 [Train  2] enters block 8 for Birmingham Interchange
06:38:48 [Train  6] arr London Old Oak Common
06:38:48 [Train  6] 10 passengers boarded
06:39:00 [Train 13] drives to starting location
06:39:18 [Train  6] enters block 1 for Birmingham Interchange
06:39:18 [Train  7] enters block 1 for London Old Oak Common
06:39:26 [Train  5] enters block 3 for Birmingham Interchange
06:39:40 [Train  4] enters block 5 for Birmingham Interchange
06:39:57 [Train  3] enters block 7 for Birmingham Interchange
06:40:00 [Train 13] 6 passengers boarded
06:40:18 [Train 13] dep London Euston
06:40:26 [Train  2] enters block 9 for Birmingham Interchange
06:41:02 [Train  0] enters block 1 for Birmingham Curzon Street
06:41:02 [Train  1] enters block 11 for Birmingham Interchange
06:42:00 [Train 14] drives to starting location
06:42:07 [Train  6] enters block 2 for Birmingham Interchange
06:42:15 [

...

07:40:24 [Train 15] enters block 7 for Birmingham Interchange
07:40:38 [Train 16] enters block 5 for Birmingham Interchange
07:40:41 [Train 10] arr Birmingham Curzon Street
07:40:41 [Train 10] 0 passengers boarded
07:40:41 [Train 10] arr final station
07:40:52 [Train 17] enters block 3 for Birmingham Interchange
07:41:06 [Train 18] arr London Old Oak Common
07:41:06 [Train 18] 0 passengers boarded
07:41:06 [Train 18] enters block 1 for Birmingham Interchange
07:41:06 [Train 19] enters block 1 for London Old Oak Common
07:41:35 [Train 11] enters block 2 for Birmingham Curzon Street
07:42:05 [Train 12] arr Birmingham Interchange
07:42:05 [Train 12] 0 passengers boarded
07:42:05 [Train 12] enters block 1 for Birmingham Curzon Street
07:42:19 [Train 13] enters block 12 for Birmingham Interchange
07:42:33 [Train 14] enters block 10 for Birmingham Interchange
07:42:47 [Train 15] enters block 8 for Birmingham Interchange
07:43:01 [Train 16] enters block 6 for Birmingham Interchange
07:43:15 [

06:43:00 [Train 14] 4 passengers boarded
06:43:12 [Train 14] dep London Euston
06:43:20 [Train  1] arr Birmingham Interchange
06:43:20 [Train  1] 5 passengers boarded
06:43:35 [Train  2] enters block 11 for Birmingham Interchange
06:43:52 [Train  3] enters block 9 for Birmingham Interchange
06:44:00 [Train  4] enters block 7 for Birmingham Interchange
06:44:27 [Train  7] arr London Old Oak Common
06:44:27 [Train  7] 7 passengers boarded
06:44:32 [Train  5] enters block 5 for Birmingham Interchange
06:44:37 [Train  6] enters block 3 for Birmingham Interchange
06:44:48 [Train  7] enters block 1 for Birmingham Interchange
06:44:48 [Train  8] enters block 1 for London Old Oak Common
06:45:00 [Train 15] drives to starting location
06:45:15 [Train  0] enters block 2 for Birmingham Curzon Street
06:45:15 [Train  1] enters block 1 for Birmingham Curzon Street
06:46:00 [Train 15] 1 passengers boarded
06:46:03 [Train 15] dep London Euston
06:46:10 [Train  2] enters block 12 for Birmingham Interc

06:22:00 [Train  7] 4 passengers boarded
06:22:12 [Train  7] dep London Euston
06:22:14 [Train  1] enters block 6 for Birmingham Interchange
06:22:18 [Train  3] arr London Old Oak Common
06:22:18 [Train  3] 6 passengers boarded
06:22:36 [Train  3] enters block 1 for Birmingham Interchange
06:22:36 [Train  4] enters block 1 for London Old Oak Common
06:23:11 [Train  0] enters block 9 for Birmingham Interchange
06:23:30 [Train  2] enters block 4 for Birmingham Interchange
06:24:00 [Train  8] drives to starting location
06:24:18 [Train  1] enters block 7 for Birmingham Interchange
06:24:40 [Train  3] enters block 2 for Birmingham Interchange
06:25:00 [Train  8] 5 passengers boarded
06:25:15 [Train  8] dep London Euston
06:25:15 [Train  0] enters block 10 for Birmingham Interchange
06:25:34 [Train  2] enters block 5 for Birmingham Interchange
06:26:22 [Train  1] enters block 8 for Birmingham Interchange
06:26:44 [Train  3] enters block 3 for Birmingham Interchange
06:27:00 [Train  9] drive

07:36:03 [Train 17] 0 passengers boarded
07:36:03 [Train 17] enters block 1 for Birmingham Interchange
07:36:03 [Train 18] enters block 1 for London Old Oak Common
07:36:21 [Train 10] enters block 2 for Birmingham Curzon Street
07:36:23 [Train 15] enters block 6 for Birmingham Interchange
07:36:43 [Train 13] enters block 11 for Birmingham Interchange
07:37:03 [Train 11] arr Birmingham Interchange
07:37:03 [Train 11] 0 passengers boarded
07:37:03 [Train 11] enters block 1 for Birmingham Curzon Street
07:37:15 [Train 16] enters block 4 for Birmingham Interchange
07:37:35 [Train 14] enters block 9 for Birmingham Interchange
07:37:55 [Train 12] enters block 14 for Birmingham Interchange
07:38:07 [Train 17] enters block 2 for Birmingham Interchange
07:38:27 [Train 15] enters block 7 for Birmingham Interchange
07:38:47 [Train 13] enters block 12 for Birmingham Interchange
07:39:19 [Train 16] enters block 5 for Birmingham Interchange
07:39:39 [Train 14] enters block 10 for Birmingham Intercha

(4, 19, 15, 4089.75)

The result of the optimization shows that the Minimum Average Travel time is 4088.99 seconds with 10 Trains per hour and 13 signaling Blocks.

N.B This is a stochastic process and will yield different result for every run. 


In [17]:
def monte_carlomax(n, xmin, xmax, ymin, ymax):
    x = [ random.randint(xmin, xmax) for i in range(n)]
    y = [ random.randint(ymin, ymax) for i in range(n)]
    xp = [ x[0] ]
    yp = [ y[0] ]
    
    #simulate
    res = runsimulation(x[0],y[0])
    _,  p = stats(res)
    
    for i in range(1, len(x)):
        #simulate
        res = runsimulation(x[i],y[i])
        _, n_p = stats(res) 
        if n_p > p:
            xp += [x[i]]
            yp += [y[i]]
            p = n_p
    
    #simulate
    res = runsimulation(xp[-1],yp[-1])
    _, pp = stats(res)
    
            
    return len(xp), xp[-1], yp[-1],pp

## Part-2

Optimize the maximum throughput of passengers in peak hours 

In [18]:
monte_carlomax(100,1,20,1,15) #run the simulation 100 for  min of 1 train and max of 20 trains, min of 1 signaling blocks and max of 15

06:00:00 [Train  0] drives to starting location
06:01:00 [Train  0] 0 passengers boarded
06:01:00 [Train  0] dep London Euston
06:01:00 [Train  0] enters block 1 for London Old Oak Common
06:03:00 [Train  1] drives to starting location
06:04:00 [Train  1] 6 passengers boarded
06:04:18 [Train  1] dep London Euston
06:06:00 [Train  0] arr London Old Oak Common
06:06:00 [Train  0] 9 passengers boarded
06:06:00 [Train  2] drives to starting location
06:06:27 [Train  0] enters block 1 for Birmingham Interchange
06:06:27 [Train  1] enters block 1 for London Old Oak Common
06:07:00 [Train  2] 9 passengers boarded
06:07:27 [Train  2] dep London Euston
06:09:00 [Train  3] drives to starting location
06:10:00 [Train  3] 8 passengers boarded
06:10:24 [Train  3] dep London Euston
06:11:27 [Train  1] arr London Old Oak Common
06:11:27 [Train  1] 7 passengers boarded
06:11:48 [Train  2] enters block 1 for London Old Oak Common
06:12:00 [Train  4] drives to starting location
06:13:00 [Train  4] 3 pas

09:01:57 [Train 18] enters block 1 for Birmingham Curzon Street
09:01:57 [Train 19] enters block 4 for Birmingham Interchange
09:03:12 [Train 17] arr Birmingham Curzon Street
09:03:12 [Train 17] 0 passengers boarded
09:03:12 [Train 17] arr final station
09:06:27 [Train 18] enters block 2 for Birmingham Curzon Street
09:09:42 [Train 19] arr Birmingham Interchange
09:09:42 [Train 19] 0 passengers boarded
09:09:42 [Train 19] enters block 1 for Birmingham Curzon Street
09:10:57 [Train 18] arr Birmingham Curzon Street
09:10:57 [Train 18] 0 passengers boarded
09:10:57 [Train 18] arr final station
09:14:12 [Train 19] enters block 2 for Birmingham Curzon Street
09:18:42 [Train 19] arr Birmingham Curzon Street
09:18:42 [Train 19] 0 passengers boarded
09:18:42 [Train 19] arr final station
06:00:00 [Train  0] drives to starting location
06:01:00 [Train  0] 1 passengers boarded
06:01:03 [Train  0] dep London Euston
06:01:03 [Train  0] enters block 1 for London Old Oak Common
06:03:00 [Train  1] dr

06:59:20 [Train  4] 10 passengers boarded
06:59:37 [Train  9] enters block 3 for Birmingham Interchange
06:59:50 [Train  4] enters block 1 for Birmingham Curzon Street
06:59:50 [Train  7] enters block 8 for Birmingham Interchange
07:00:12 [Train 10] arr London Old Oak Common
07:00:12 [Train 10] 5 passengers boarded
07:00:16 [Train  5] enters block 13 for Birmingham Interchange
07:00:27 [Train 10] enters block 1 for Birmingham Interchange
07:00:27 [Train 11] enters block 1 for London Old Oak Common
07:01:01 [Train  8] enters block 6 for Birmingham Interchange
07:01:05 [Train  6] enters block 11 for Birmingham Interchange
07:01:50 [Train  9] enters block 4 for Birmingham Interchange
07:02:03 [Train  7] enters block 9 for Birmingham Interchange
07:02:29 [Train  5] enters block 14 for Birmingham Interchange
07:02:39 [Train 10] enters block 2 for Birmingham Interchange
07:03:14 [Train  8] enters block 7 for Birmingham Interchange
07:03:18 [Train  6] enters block 12 for Birmingham Interchang

06:01:06 [Train  0] enters block 1 for London Old Oak Common
06:03:00 [Train  1] drives to starting location
06:04:00 [Train  1] 10 passengers boarded
06:04:30 [Train  1] dep London Euston
06:06:00 [Train  2] drives to starting location
06:06:06 [Train  0] arr London Old Oak Common
06:06:06 [Train  0] 12 passengers boarded
06:06:42 [Train  0] enters block 1 for Birmingham Interchange
06:06:42 [Train  1] enters block 1 for London Old Oak Common
06:07:00 [Train  2] 6 passengers boarded
06:07:18 [Train  2] dep London Euston
06:09:00 [Train  3] drives to starting location
06:10:00 [Train  3] 3 passengers boarded
06:10:09 [Train  3] dep London Euston
06:10:34 [Train  0] enters block 2 for Birmingham Interchange
06:11:42 [Train  1] arr London Old Oak Common
06:11:42 [Train  1] 10 passengers boarded
06:12:00 [Train  4] drives to starting location
06:12:12 [Train  1] enters block 1 for Birmingham Interchange
06:12:12 [Train  2] enters block 1 for London Old Oak Common
06:13:00 [Train  4] 7 pas

07:30:03 [Train  8] 0 passengers boarded
07:30:03 [Train  8] arr final station
07:30:28 [Train 12] enters block 6 for Birmingham Interchange
07:31:06 [Train 16] arr London Old Oak Common
07:31:06 [Train 16] 0 passengers boarded
07:31:06 [Train 16] enters block 1 for Birmingham Interchange
07:31:06 [Train 17] enters block 1 for London Old Oak Common
07:31:09 [Train  9] enters block 2 for Birmingham Curzon Street
07:31:36 [Train 13] enters block 5 for Birmingham Interchange
07:32:00 [Train 10] arr Birmingham Interchange
07:32:00 [Train 10] 0 passengers boarded
07:32:00 [Train 10] enters block 1 for Birmingham Curzon Street
07:32:43 [Train 14] enters block 4 for Birmingham Interchange
07:33:13 [Train 11] enters block 8 for Birmingham Interchange
07:33:51 [Train 15] enters block 3 for Birmingham Interchange
07:34:21 [Train 12] enters block 7 for Birmingham Interchange
07:34:58 [Train 16] enters block 2 for Birmingham Interchange
07:35:28 [Train 13] enters block 6 for Birmingham Interchange

...

06:52:00 [Train 17] 8 passengers boarded
06:52:16 [Train  6] enters block 6 for Birmingham Interchange
06:52:24 [Train 17] dep London Euston
06:52:36 [Train  7] enters block 4 for Birmingham Interchange
06:52:50 [Train  8] enters block 2 for Birmingham Interchange
06:53:39 [Train  3] arr Birmingham Interchange
06:53:39 [Train  3] 9 passengers boarded
06:53:57 [Train  1] arr Birmingham Curzon Street
06:53:57 [Train  1] 0 passengers boarded
06:53:57 [Train  1] arr final station
06:53:57 [Train  2] enters block 2 for Birmingham Curzon Street
06:54:00 [Train 18] drives to starting location
06:54:06 [Train  3] enters block 1 for Birmingham Curzon Street
06:54:11 [Train  4] enters block 11 for Birmingham Interchange
06:54:34 [Train  5] enters block 9 for Birmingham Interchange
06:54:51 [Train  6] enters block 7 for Birmingham Interchange
06:55:00 [Train 18] 7 passengers boarded
06:55:11 [Train  7] enters block 5 for Birmingham Interchange
06:55:15 [Train  9] arr London Old Oak Common
06:55:1

06:16:59 [Train  0] enters block 3 for Birmingham Interchange
06:17:15 [Train  2] arr London Old Oak Common
06:17:15 [Train  2] 7 passengers boarded
06:17:25 [Train  1] enters block 2 for Birmingham Interchange
06:17:36 [Train  2] enters block 1 for Birmingham Interchange
06:17:36 [Train  3] enters block 1 for London Old Oak Common
06:18:00 [Train  6] drives to starting location
06:19:00 [Train  6] 3 passengers boarded
06:19:09 [Train  6] dep London Euston
06:21:00 [Train  7] drives to starting location
06:22:00 [Train  7] 7 passengers boarded
06:22:09 [Train  0] enters block 4 for Birmingham Interchange
06:22:21 [Train  7] dep London Euston
06:22:35 [Train  1] enters block 3 for Birmingham Interchange
06:22:36 [Train  3] arr London Old Oak Common
06:22:36 [Train  3] 5 passengers boarded
06:22:46 [Train  2] enters block 2 for Birmingham Interchange
06:22:51 [Train  3] enters block 1 for Birmingham Interchange
06:22:51 [Train  4] enters block 1 for London Old Oak Common
06:24:00 [Train 

07:21:06 [Train 15] enters block 1 for London Old Oak Common
07:21:40 [Train 10] enters block 5 for Birmingham Interchange
07:21:40 [Train 11] enters block 4 for Birmingham Interchange
07:21:40 [Train 12] enters block 3 for Birmingham Interchange
07:21:40 [Train 13] enters block 2 for Birmingham Interchange
07:21:40 [Train 14] enters block 1 for Birmingham Interchange
07:22:39 [Train  6] arr Birmingham Curzon Street
07:22:39 [Train  6] 0 passengers boarded
07:22:39 [Train  6] arr final station
07:23:19 [Train  7] enters block 2 for Birmingham Curzon Street
07:23:59 [Train  8] arr Birmingham Interchange
07:23:59 [Train  8] 0 passengers boarded
07:23:59 [Train  8] enters block 1 for Birmingham Curzon Street
07:23:59 [Train  9] enters block 6 for Birmingham Interchange
07:26:06 [Train 15] arr London Old Oak Common
07:26:06 [Train 15] 0 passengers boarded
07:26:06 [Train 16] enters block 1 for London Old Oak Common
07:26:50 [Train 11] enters block 5 for Birmingham Interchange
07:26:50 [Tra

06:44:24 [Train  7] 8 passengers boarded
06:44:48 [Train  7] enters block 1 for Birmingham Interchange
06:44:48 [Train  8] enters block 1 for London Old Oak Common
06:44:52 [Train  1] arr Birmingham Interchange
06:44:52 [Train  1] 5 passengers boarded
06:45:00 [Train 15] drives to starting location
06:45:07 [Train  2] enters block 8 for Birmingham Interchange
06:45:30 [Train  0] enters block 2 for Birmingham Curzon Street
06:45:30 [Train  1] enters block 1 for Birmingham Curzon Street
06:45:37 [Train  5] enters block 4 for Birmingham Interchange
06:46:00 [Train 15] 4 passengers boarded
06:46:12 [Train 15] dep London Euston
06:46:15 [Train  3] enters block 7 for Birmingham Interchange
06:47:09 [Train  6] enters block 3 for Birmingham Interchange
06:47:52 [Train  4] enters block 6 for Birmingham Interchange
06:48:00 [Train 16] drives to starting location
06:48:40 [Train  7] enters block 2 for Birmingham Interchange
06:49:00 [Train  2] arr Birmingham Interchange
06:49:00 [Train  2] 2 pass

(3, 5, 8, 298.0)

OPTIMIZING THE MAXIMUM THROUGHPUT OF PASSENGERS IN PEAK HOURS

The result of the optimization shows that Nine (9) Trains per hour and Ten (10) signaling blocks gives a maximum of 300 passengers in peak hours. 

N.B This is a stochastic process and will yield different result for every run. 



# Discussion and Results 


We first set up a simulation of the Train Network for optimal 'n' trains per hour with 'k' no signal blocks, taking into account the number of passengers per hour and the signal blocks of the rail lines in order to achieve optimum simulation performance. Signal blocks are designed to avoid collisions and delay between the movements of the Trains using Simpy Resource.

The simulation result is integrated into the Monte Carlo optimization to minimize the total travel time of the Trains and to optimize the number of passengers boarding the Train at any given time. Using Poisson Distribution, we predicted that a number of passengers will arrive at the train at a given hour, the average boarding time for each passenger was believed to be 3 seconds, because it is not possible for everyone to get on board due to a tight schedule at each station. Also, passengers who are not at a stop before the arrival of the train do not get on board. More precisely, we assumed that the total number of potential passengers at each stop at any given time was 100, so the process is specified for the pick-up of passengers arriving at the station prior to the arrival of the train.

We used the MonteCarlo Optimization method to get the optimal travel time and number of passengers for the simulation proposed. The results show that the total average travel time is 4088.99 seconds with 10 trains and 12 signal blocks, including a maximum throughput of 300 passengers an hour with 9 trains and 10 signal blocks.


# References 


[1] SimPy, "Documentation for SimPy," 2020. [Online]. Available: https://simpy.readthedocs.io/en/latest/simpy_intro/installation.html [Accessed on: May. 6, 2020].

[2] A.B. Downey, Modelling and Simulation in Python, 3rd ed. Needham, Massachusetts: Green Tea Press, 2017.

[3] D. Abbott, and M.V. Marinov, "An event based simulation model to evaluate the design of a rail interchange yard, which provides service to high speed and conventional railways," Simulation Modelling Practice and Theory, Vol. 52, pp.15-39, Jan. 2015. doi:10.1016/j.simpat.2014.12.003

